In [735]:
import pandas as pd
import word2vec as w2v
import nltk
import Stemmer
import time
import numpy as np

In [945]:
root = "/Users/nikita/Documents/python_3_filies/ML/mvideo/data/"
data = pd.read_csv(root + "X_train.csv", delimiter=",")

In [946]:
data.describe()

sku  categoryLevel1Id  categoryLevel2Id       brandId  \
count  1.558700e+04      15587.000000      1.558700e+04  15587.000000   
mean   2.470460e+07        341.629435      3.427723e+06    444.753577   
std    1.028728e+07        119.478142      1.186588e+06    494.612637   
min    1.000027e+06        101.000000      1.010102e+06      1.000000   
25%    2.000459e+07        207.000000      2.070202e+06     48.000000   
50%    2.002190e+07        405.000000      4.050206e+06     93.000000   
75%    3.001108e+07        411.000000      4.110102e+06    787.000000   
max    5.004011e+07        701.000000      7.010101e+06   2159.000000   

             reting  
count  15587.000000  
mean       4.118496  
std        1.316966  
min        1.000000  
25%        4.000000  
50%        5.000000  
75%        5.000000  
max        5.000000

In [947]:
data.corr()

sku  categoryLevel1Id  categoryLevel2Id   brandId  \
sku               1.000000          0.130009          0.144646  0.227148   
categoryLevel1Id  0.130009          1.000000          0.996477  0.069459   
categoryLevel2Id  0.144646          0.996477          1.000000  0.089441   
brandId           0.227148          0.069459          0.089441  1.000000   
reting            0.018114         -0.050502         -0.048936 -0.040026   

                    reting  
sku               0.018114  
categoryLevel1Id -0.050502  
categoryLevel2Id -0.048936  
brandId          -0.040026  
reting            1.000000

In [948]:
data.head()

sku  categoryLevel1Id  categoryLevel2Id  brandId  \
0  20005023               401           4010201      826   
1  20020647               403           4030101     1425   
2  20020701               401           4010401      124   
3  30012256               203           2030301       93   
4  30011341               205           2050201      656   

                                            property  \
0  [{34: 'f982777489055c6563d68c005fd24aad'}, {36...   
1  [{34: '9ce895413ebdf6b6dcb69b07dc782591'}, {36...   
2  [{34: '9ce895413ebdf6b6dcb69b07dc782591'}, {36...   
3  [{34: '9ce895413ebdf6b6dcb69b07dc782591'}, {36...   
4  [{34: '9ce895413ebdf6b6dcb69b07dc782591'}, {36...   

                           userName  reting        date  \
0  b2898a81b45310b30beb8fc0c0a9ce1e     2.0  2013-06-28   
1  538c73d64461e13907bb95c51c38bfbc     2.0  2010-07-04   
2  ddca2d0101513a6209db7868eed8be05     4.0  2010-05-27   
3  289c20015b3713a82ba5ddf774d996f7     5.0  2016-10-11   
4  5576f82d149d4f688644fef2322c63ef     5.0  2010-02-26   

                                             comment commentNegative  \
0  2,5 года работала и все...устала! Лампочка гор...             NaN   
1  Через 2 месяца после истечении гарантийного ср...             NaN   
2  пользуюсь уже три недели. нареканий ни каких н...             NaN   
3  Ребят этот системный блок подойдёт для игры кс...             NaN   
4  я считаю, что яри замечательный телефон! Прият...             NaN   

  commentPositive  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN

In [949]:
comments = data.comment
rating = data.reting


# train data preparation

In [811]:
text_pre = open(root + 'nik_texts_pre_large.txt')

In [812]:
text_pre = text_pre.read()

In [825]:
# так работает tokenizer для русского и не только)
test = "Привет, как дела?\n хорошо» * ; \n\n hello. Еда - ср. оно. Hi он." # 
test1 = 'Hello. How are u? norm.'
tok = nltk.tokenize.toktok.ToktokTokenizer()
# токены слов
print(tok.tokenize(test))
# токины предложений
sents = tok.tokenize_sents(tok.tokenize(test))
print(sents)


['Привет', ',', 'как', 'дела', '?', 'хорошо', '»', '*', ';', 'hello.', 'Еда', '-', 'ср.', 'оно.', 'Hi', 'он', '.']
[['Привет'], [','], ['как'], ['дела'], ['?'], ['хорошо'], ['»'], ['*'], [';'], ['hello', '.'], ['Еда'], ['-'], ['ср', '.'], ['оно', '.'], ['Hi'], ['он'], ['.']]


In [826]:
sents

[['Привет'],
 [','],
 ['как'],
 ['дела'],
 ['?'],
 ['хорошо'],
 ['»'],
 ['*'],
 [';'],
 ['hello', '.'],
 ['Еда'],
 ['-'],
 ['ср', '.'],
 ['оно', '.'],
 ['Hi'],
 ['он'],
 ['.']]

In [1176]:
# оставляет только слова без знаков и сокращений
def make_only_words(data, verbose=True):
    result = []
    #signes = [",", ".", "?" ,"!" ,"-", "_", ":", ";", "'", '"']
    signs = ",.?!-_—:'()[]«»*;...'" + '"'
    length = len(data)
    i = 0
    proc = 0
    if length:
        while i < length:
            sent = data[i]
            if len(sent) == 2 and sent[-1] == '.':
                del(data[i][-1])
            elif len(sent) == 1 and sent[-1] in signs:
                del(data[i])
                length -= 1
                i -= 1
            proc = i/length * 100
            if verbose and i % (int(length/7)) == 0:
                print("process: ", int(proc), "%")
            i += 1
        if verbose:
            print("finish")

        for i, sent in enumerate(data):
            data[i] = sent[-1]    
        return 0
    else:
        print('zero length')
        return 1

In [828]:
make_only_words(sents)

process:  0 %
process:  0 %
process:  12 %
process:  13 %
process:  23 %
process:  25 %
process:  33 %
process:  41 %
process:  45 %
process:  54 %
process:  63 %
process:  72 %
process:  81 %
process:  90 %
finish


In [829]:
sents

['Привет', 'как', 'дела', 'хорошо', 'hello', 'Еда', 'ср', 'оно', 'Hi', 'он']

# прочитай обязятельно про это - nltk.scikitlearn

In [791]:
# words_pre = tok.tokenize_sents(tok.tokenize(text_pre))
words_pre_copy = words_pre[: ]
len(words_pre)

1581652

In [792]:
len(words_pre_copy)

1581652

In [793]:
len(words_pre_copy)/len(words_pre)*100

100.0

In [794]:
# очитска от знаков препинания
start = time.clock()
make_only_words(words_pre_copy)
end = time.clock()
print("Time required: {:.2f} sec.".format(end-start))


process:  0 %
process:  14 %
process:  14 %
process:  28 %
process:  42 %
process:  42 %
process:  57 %
process:  71 %
process:  85 %
process:  99 %
finish
Time required: 307.40 sec.


In [795]:
len(words_pre_copy)

1138713

In [797]:
#words_pre_all = words_pre_copy[:]

In [798]:
1 - len(np.unique(words_pre_copy))/len(words_pre_copy)

0.8270995413242845

In [922]:
def stem_words(words, verbose=True):
    stemmer = nltk.stem.SnowballStemmer('russian')
    length = len(words)
    proc = 0
    for i, word in enumerate(words):
        words[i] = stemmer.stem(word)
        proc = i/length * 100
        if verbose and i % (int(length/7)) == 0:
            print("process: ", int(proc), "%")
    print('finish \n')
    
def stem(word):
    stemmer = nltk.stem.SnowballStemmer('russian')
    return stemmer.stem(word)

In [800]:
len(words_pre_copy)

1138713

In [801]:
# осторожно, занимает много времени
start = time.clock()
words_pre_stemmed = stem_words(words_pre_copy)
end = time.clock()
print("Time required: {:.2} sec.".format(end-start))


process:  0 %
process:  14 %
process:  28 %
process:  42 %
process:  57 %
process:  71 %
process:  85 %
process:  99 %
finish 

Time required: 1.1e+02 sec.


In [802]:
len(words_pre_copy)

1138713

In [803]:
1 - len(np.unique(words_pre_copy))/len(words_pre_copy)

0.9321339090710302

In [805]:
#words_pre_all_stemmed = words_pre_copy[:]

In [818]:
words_pre_all_stemmed_str = ""
for w in words_pre_all_stemmed:
    words_pre_all_stemmed_str += w + ' '

In [819]:
words_pre_all_stemmed_str

'крошк сын к отц пришел и спрос крох что так хорош и что так плох у мен секрет нет слуша детишк пап эт ответ помеща в книжк есл ветер крыш рвет есл град загроха кажд знает эт вот для прогулок плох дожд покапа и прошел солнц в цел свет эт очен хорош и больш и дет есл сын черн ноч гряз леж на рожиц ясн эт плох очен для ребяч кожиц есл мальчик люб мыл и зубн порошок этот мальчик очен мил поступа хорош есл бьет дрян драчун слаб мальчишк я так не хоч даж встав в книжк этот вот крич не трож тех кто меньш рост этот мальчик так хорош загляден прост есл ты порва подряд книжиц и мячик октябрят говор плоховат мальчик есл мальчик люб труд тычет в книжк пальчик про так пишут тут он хорош мальчик от ворон карапуз убежа заоха мальчик этот прост трус эт очен плох этот хот и сам с вершок спор с грозн птиц храбр мальчик хорош в жизн пригод этот в гряз полез и рад что грязн рубах про так говор он плох нерях этот чист валенк моет сам галош он хот и маленьк но вполн хорош помн эт кажд сын зна люб ребенок в

In [831]:


#cleared_text = text_pre = open(root + 'nik_texts_pre_cleared_large_v1.txt', mode='w')

In [832]:
#cleared_text.write(str(words_pre_all_stemmed_str))

5894534

# 1 просмотр по словам

In [899]:
rating[20]

5.0

In [1286]:
comments[20]

'Прекрасный телевизор!!!Качество изображения на высоте,не уступает плазме!Звук басистый,объёмный. Меню понятное,настройки продвинутые.А главное Малазийской сборки. Советую ВСЕМ!!!'

In [1287]:
words_pre_all_stemmed.count('гл')

14

# обучение w2v

In [995]:
import word2vec
from scipy.spatial import distance

In [916]:
#word2vec.word2vec( rootpath+'much_data.txt', rootpath+'much_data-phrases.bin', size=1000, window=15,  )  
word2vec.word2vec( root+'nik_texts_pre_cleared_large_v1.txt', root+'-nik_texts_pre_cleared_large_v1_w2v.bin', size=200, window=18, min_count=2 )#read_vocab=rootpath+history+'-clusters.txt')  


print('ENd')

ENd


In [918]:
model = word2vec.load(root+'-nik_texts_pre_cleared_large_v1_w2v.bin')

In [921]:
len(model.vocab)

39484

In [928]:
indexes, metrics = model.cosine(stem('прекрасно'),10)
model.generate_response(indexes, metrics).tolist()

[('малозначительн', 0.8592771399947529),
 ('мудрост', 0.8116763730763328),
 ('нереальн', 0.8013841235072809),
 ('красот', 0.7951365772574851),
 ('удивительн', 0.7932000807239796),
 ('почтен', 0.7867102229997829),
 ('нечт', 0.7838119358904914),
 ('божеск', 0.7817061900990921),
 ('потешн', 0.7765611161555757),
 ('простот', 0.7744357855044255)]

# подготовка комментария

In [1341]:
#comments_copy = comments[:]
test = list(comments[:10])

In [1342]:
test = list(test)

In [1343]:
sents = []

In [1344]:
for sent in test:
    sents.append(tok.tokenize_sents(tok.tokenize(sent)))

In [1345]:
sents[0]

[['2,5'],
 ['года'],
 ['работала'],
 ['и'],
 ['все'],
 ['...'],
 ['устала'],
 ['!'],
 ['Лампочка'],
 ['горит'],
 ['и'],
 ['больше'],
 ['ничего'],
 ['!']]

In [1346]:
# сделать return в функции
sents_words = []
for i,sent in enumerate(sents):
    make_only_words(sent, verbose=False)
    sents_words.append(sent)

In [1347]:
sents_words[3]

['Ребят',
 'этот',
 'системный',
 'блок',
 'подойдёт',
 'для',
 'игры',
 'кс',
 'го',
 'на',
 'средних',
 'гастройках']

In [1295]:
def dist(a, b):
    # В последствии могут пригодится и другие расстояния
    return distance.cosine(a, b)

In [1373]:
def get_resulting_vector(sentence):
    resulting_vector = np.zeros(len(model.get_vector(model.vocab[0])))
    for word in sentence:
        # try работает быстрее, нежели проверять наличие слова в словаре
        try:
            vector_word = model.get_vector(word)
            resulting_vector += vector_word
        except KeyError:
            pass
    return resulting_vector

In [1375]:
vec = get_resulting_vector(sents_words[3])

In [1298]:
vec_key = model.get_vector(stem('советую'))

In [1299]:
dist(vec_key, vec)

0.44690460742949756

In [1300]:
rating[3]

5.0

In [1302]:
len(vec_data)

500

In [1303]:
def tree_near_word(word, num_leafs=10):
    try:
        indexes, metrics = model.cosine(word, num_leafs)
        words_leaf = []
        vecs_words_leaf = []
        for i in indexes:
            word_leaf = model.vocab[i]
            vec_word_leaf = model.get_vector(word_leaf)
            words_leaf.append(word_leaf)
            vecs_words_leaf.append(vec_word_leaf)
        return words_leaf, vecs_words_leaf
    except KeyError:
        return 0,0

In [1304]:
stem('не')

'не'

In [1305]:
words, vecs = tree_near_word(stem('хорошо'))

In [1306]:
words

['добр',
 'жела',
 'плох',
 'божеск',
 'правд',
 'вам',
 'успех',
 'желан',
 'мо',
 'трудн']

In [1307]:
good_words = ['хорошо', 'отлично', 'идеально', 'прекрасно', 'удобно', 'превосходно',  'советую', 'рекомендую',
              'наслаждаюсь', 'кайфую', 'кайф', 'балдею', 'хвалю']

bad_words = ['плохо', 'ужасно', 'ужас', 'отвратительно', 'сломалось']

In [1308]:
len(good_words)

13

In [1309]:
for word in good_words:
    print(tree_near_word(stem(word), 3)[0])

['добр', 'жела', 'плох']
['исключительн', 'важн', 'уч']
['практическ', 'принцип', 'производительн']
['малозначительн', 'мудрост', 'нереальн']
['чтен', 'розыск', 'обязательств']
['поразительн', 'весьм', 'спешн']
['учител', 'принят', 'обяза']
['предлож', 'приня', 'доставлен']
['бессвязн', 'мистическ', 'поучен']
['одича', 'крюч', 'семидесятипятилет']
['одича', 'крюч', 'семидесятипятилет']
0
['хваста', 'обманыва', 'глупост']


In [1310]:
for word in bad_words:
    print(tree_near_word(stem(word), 3)[0])

['неприятн', 'хорош', 'трудн']
['наводя', 'беспорядок', 'шумн']
['страх', 'сон', 'страшн']
['бессмыслен', 'парен', 'гадк']
['слом', 'изнутр', 'обв']


In [1311]:
indexes, metrics = model.analogy(['очен', 'плох'], [],)

In [1312]:
model.generate_response(indexes, metrics).tolist()

[('серьез', 0.8189016690121154),
 ('приятн', 0.8110246504372036),
 ('намек', 0.8099426742898651),
 ('незначительн', 0.8071640958251323),
 ('неинтересн', 0.7993046665773167),
 ('неприятн', 0.7990016954138431),
 ('страшн', 0.790038144208591),
 ('хорош', 0.7838732502788033),
 ('мил', 0.783265561531183),
 ('мудрен', 0.783063703416784)]

In [1586]:
# очистка от малых слов
def del_little_words(words, leave_deny=True):
    length = len(words)
    i = 0
    while i < length:
        if len(words[i]) <= 3:
            if leave_deny and words[i] != 'не':
                del(words[i])
            elif not leave_deny:
                del(words[i])
            i -= 1
            length -= 1
        i += 1

In [1580]:
type(sents_words[3])

list

In [1581]:
test = ['Привет', 'как', 'дела', 'а', 'не', 'hello']


In [1582]:
del_little_words(test, leave_deny=True)

1 как
1 а


In [1583]:
test

['Привет', 'дела', 'не', 'hello']

In [1564]:
tmp = sents_words[4][:]

In [1384]:
tmp

['считаю',
 'замечательный',
 'телефон',
 'Приятно',
 'держать',
 'руке',
 'удобные',
 'кнопки',
 'Конечно',
 'больше',
 'подходит',
 'молодежи',
 'наверное',
 'рассчитан',
 'публику',
 'телефоне',
 'лично',
 'вижу',
 'никаких',
 'недостатков',
 'Советую',
 'брать',
 'такой',
 'задумываться']

In [1369]:
for i in tmp:
    try:
        vec_p = model.get_vector(stem('прил'))
        vec_tmp = model.get_vector(stem(i))
        print(i, dist(vec_p, vec_tmp))
    except:
        pass

Сегодня 1.24457676088
купила 0.950228206803
таких 0.884524381339
Ужасный 1.04091282339
Скорости 0.814428990932
хватает 1.16995872068
вообще 0.800194164252
включается 0.668645491042
еле-еле 1.17618645794
только 1.14145097426
скорости 0.814428990932
остальных 1.20042548261
быстро 1.22351319097
останавливается 1.1104987806
если 1.19222563549
конечно 0.931654029273
запускается 0.941379624606


In [1396]:
tmp

['считаю',
 'замечательный',
 'телефон',
 'Приятно',
 'держать',
 'руке',
 'удобные',
 'кнопки',
 'Конечно',
 'больше',
 'подходит',
 'молодежи',
 'наверное',
 'рассчитан',
 'публику',
 'телефоне',
 'лично',
 'вижу',
 'никаких',
 'недостатков',
 'Советую',
 'брать',
 'такой',
 'задумываться']

In [1385]:
vec_1 = get_resulting_vector(sents_words[4])

In [1405]:
vec_good = model.get_vector(stem('удобно'))

In [1406]:
dist(vec_1, vec_good)

0.39867717532870117

In [1587]:
vec_data = []
train_size = 500
for i, comment in enumerate(comments[:train_size]):
    comment = tok.tokenize_sents(tok.tokenize(comment))
    make_only_words(comment, verbose=False)
    del_little_words(comment)
    vec = get_resulting_vector(comment)
    vec_data.append(vec)

#  Обучение модели предсказания

In [1588]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor



In [1589]:
X_train, X_test, y_train, y_test = train_test_split(
    vec_data, rating[:train_size], test_size=0.4, random_state=0)

#X_train.shape, y_train.shape

#X_test.shape, y_test.shape


regr = RandomForestRegressor()
regr.fit(X_train, y_train)

RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_split=1e-07, min_samples_leaf=1,
           min_samples_split=2, min_weight_fraction_leaf=0.0,
           n_estimators=10, n_jobs=1, oob_score=False, random_state=None,
           verbose=0, warm_start=False)

In [1590]:
regr.score(X_test, y_test)

-0.078389245653053718

In [1519]:
#regr.predict(vec_data[7])